In [ ]:
!wget https://storage.googleapis.com/deepmind-media/Datasets/kinetics700_2020.tar.gz

In [ ]:
!tar -xf kinetics700_2020.tar.gz

In [ ]:
import pandas as pd

df = pd.read_csv('/content/kinetics700_2020/train.csv')

unique_labels = df['label'].unique()

for i, label in enumerate(unique_labels):
    print(f"{i}- {label}")

In [ ]:
def merge_files(real_labels_file, gpt_labels_file):
    with open(real_labels_file, 'r') as real_file, open(gpt_labels_file, 'r') as gpt_file:
        real_labels = real_file.readlines()
        gpt_labels = gpt_file.readlines()

    merged_labels = []
    for real, gpt in zip(real_labels, gpt_labels):
        real_label = real.split('-')[1].strip()
        gpt_label = gpt.split('-')[1].strip()

        # Merge the labels and add to the list
        merged_labels.append(f'{real_label}: {gpt_label}')

    return merged_labels

real_labels_file = '/content/real-labels.txt'
gpt_labels_file = '/content/chatgpt-labels.txt'

merged_labels = merge_files(real_labels_file, gpt_labels_file)

In [ ]:
!pip install transformers

In [ ]:
from transformers import CLIPProcessor, CLIPModel

model = CLIPModel.from_pretrained("openai/clip-vit-large-patch14")
processor = CLIPProcessor.from_pretrained("openai/clip-vit-large-patch14")

In [ ]:
with open('enhanced-kinetics-label-CLIP-embedding.txt', 'w') as write_file:
    for label in merged_labels:
        text_inputs = processor(text=label, return_tensors="pt", padding=True)
        text_features = model.get_text_features(**text_inputs).float()
        # format output to only have 4 digits after decimal point
        formatted_features = ['{:.4f}'.format(val) for val in text_features[0].tolist()]
        write_file.write(label.replace(':', ' |') + ' | ' + str(formatted_features) + '\n')

In [ ]:
!wget https://www.crcv.ucf.edu/data/UCF101/UCF101TrainTestSplits-RecognitionTask.zip --no-check-certificate
!unzip UCF101TrainTestSplits-RecognitionTask.zip

--2023-08-02 13:01:00--  https://www.crcv.ucf.edu/data/UCF101/UCF101TrainTestSplits-RecognitionTask.zip
Resolving www.crcv.ucf.edu (www.crcv.ucf.edu)... 132.170.214.127
Connecting to www.crcv.ucf.edu (www.crcv.ucf.edu)|132.170.214.127|:443... connected.
  Unable to locally verify the issuer's authority.
HTTP request sent, awaiting response... 200 OK
Length: 113943 (111K) [application/zip]
Saving to: ‘UCF101TrainTestSplits-RecognitionTask.zip’

UCF101TrainTestSpli 100%[===================>] 111.27K  --.-KB/s    in 0.05s   

2023-08-02 13:01:00 (2.03 MB/s) - ‘UCF101TrainTestSplits-RecognitionTask.zip’ saved [113943/113943]

Archive:  UCF101TrainTestSplits-RecognitionTask.zip
   creating: ucfTrainTestlist/
  inflating: ucfTrainTestlist/classInd.txt  
  inflating: ucfTrainTestlist/testlist01.txt  
  inflating: ucfTrainTestlist/testlist02.txt  
  inflating: ucfTrainTestlist/testlist03.txt  
  inflating: ucfTrainTestlist/trainlist01.txt  
  inflating: ucfTrainTestlist/trainlist02.txt  
  inf

In [ ]:
with open('enhanced-ucf-101-label-CLIP-embedding.txt', 'w') as write_file:
  with open('ucf101-labels.txt', 'r') as ucf101_labels_file:
    ucf101_labels = ucf101_labels_file.readlines()
    for label in ucf101_labels:
          text_inputs = processor(text=label, return_tensors="pt", padding=True)
          text_features = model.get_text_features(**text_inputs).float()
          # format output to only have 4 digits after decimal point
          formatted_features = ['{:.4f}'.format(val) for val in text_features[0].tolist()]
          write_file.write(label.replace(':', ' |') + ' | ' + str(formatted_features) + '\n')